### Extracting Featues of the 2020 Movies from Wikipedia

In [1]:
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import requests
import bs4 as bs
import urllib.request

In [2]:
link = 'https://en.wikipedia.org/wiki/List_of_American_films_of_2020'

In [3]:
source = urllib.request.urlopen(link).read()
soup = bs.BeautifulSoup(source , 'lxml')

In [4]:
tables = soup.find_all('table' , class_='wikitable sortable')

In [5]:
df1 = pd.read_html(str(tables[0]))[0]
df2 = pd.read_html(str(tables[1]))[0]
df3 = pd.read_html(str(tables[2]))[0]
df4 = pd.read_html(str(tables[3]).replace("'1\"\'",'"1"'))[0] # avoided "ValueError: invalid literal for int() with base 10: '1"'

In [6]:
df = df1.append(df2.append(df3.append(df4 , ignore_index=True) , ignore_index=True) , ignore_index=True)

In [7]:
df

Opening  Opening.1                  Title  \
0     JANUARY          3             The Grudge   
1     JANUARY         10             Underwater   
2     JANUARY         10            Like a Boss   
3     JANUARY         10          Three Christs   
4     JANUARY         10      Inherit the Viper   
..        ...        ...                    ...   
270  DECEMBER         25       We Can Be Heroes   
271  DECEMBER         25      News of the World   
272  DECEMBER         25  One Night in Miami...   
273  DECEMBER         25  Promising Young Woman   
274  DECEMBER         30      Pieces of a Woman   

                                    Production company  \
0    Screen Gems / Stage 6 Films / Ghost House Pict...   
1    20th Century Fox / TSG Entertainment / Chernin...   
2                   Paramount Pictures / Artists First   
3                                            IFC Films   
4    Lionsgate / Barry Films / Tycor International ...   
..                                                 ...   
270  Netflix / Troublemaker Studios / Double R Prod...   
271  Universal Pictures / Playtone / Perfect World ...   
272                                     Amazon Studios   
273          Focus Features / FilmNation Entertainment   
274                             Netflix / Bron Studios   

                                         Cast and crew  \
0    Nicolas Pesce (director/screenplay); Andrea Ri...   
1    William Eubank (director); Brian Duffield, Ada...   
2    Miguel Arteta (director); Sam Pitman, Adam Col...   
3    Jon Avnet (director/screenplay); Eric Nazarian...   
4    Anthony Jerjen (director); Andrew Crabtree (sc...   
..                                                 ...   
270  Robert Rodriguez (director/screenplay); Priyan...   
271  Paul Greengrass (director/screenplay); Luke Da...   
272  Regina King (director); Kemp Powers (screenpla...   
273  Emerald Fennell (director/screenplay); Carey M...   
274  Kornél Mundruczó (director); Kata Wéber (scree...   

    .mw-parser-output .tooltip-dotted{border-bottom:1px dotted;cursor:help}Ref.  \
0                                                  [2]                            
1                                                  [3]                            
2                                                  [4]                            
3                                                  NaN                            
4                                                  [5]                            
..                                                 ...                            
270                                                NaN                            
271                                                NaN                            
272                                                NaN                            
273                                                NaN                            
274                                                NaN                            

      Ref.  
0      NaN  
1      NaN  
2      NaN  
3      NaN  
4      NaN  
..     ...  
270  [243]  
271  [244]  
272  [245]  
273  [246]  
274  [247]  

[275 rows x 7 columns]

In [8]:
df_2020 = df[['Title' , 'Cast and crew']]

In [9]:
df_2020

Title                                      Cast and crew
0               The Grudge  Nicolas Pesce (director/screenplay); Andrea Ri...
1               Underwater  William Eubank (director); Brian Duffield, Ada...
2              Like a Boss  Miguel Arteta (director); Sam Pitman, Adam Col...
3            Three Christs  Jon Avnet (director/screenplay); Eric Nazarian...
4        Inherit the Viper  Anthony Jerjen (director); Andrew Crabtree (sc...
..                     ...                                                ...
270       We Can Be Heroes  Robert Rodriguez (director/screenplay); Priyan...
271      News of the World  Paul Greengrass (director/screenplay); Luke Da...
272  One Night in Miami...  Regina King (director); Kemp Powers (screenpla...
273  Promising Young Woman  Emerald Fennell (director/screenplay); Carey M...
274      Pieces of a Woman  Kornél Mundruczó (director); Kata Wéber (scree...

[275 rows x 2 columns]

In [10]:
from tmdbv3api import TMDb
import json
import requests
tmdb = TMDb()
tmdb.api_key = 'fce0af3409e6113c9b3c75aaf49341bb'

In [11]:
from tmdbv3api import Movie
tmdb_movie = Movie() 
def get_genre(x):
    genres = []
    try:
        result = tmdb_movie.search(x)
        print(f"Search result for '{x}': {result}")  # Debug print
        if not result:
            print("No results found.")
            return np.NaN
        else:
            movie = result[0]
            print(f"First movie in result: {movie}")  # Debug print
            movie_id = getattr(movie, 'id', None)
            if movie_id:
                response = requests.get(f'https://api.themoviedb.org/3/movie/{movie_id}?api_key={tmdb.api_key}')
                data_json = response.json()
                print(f"API response for movie ID {movie_id}: {data_json}")  # Debug print
                if 'genres' in data_json and data_json['genres']:
                    genre_str = " "
                    for genre in data_json['genres']:
                        genres.append(genre['name'])
                    return genre_str.join(genres)
                else:
                    print("No genres found in movie data.")
                    return np.NaN
            else:
                print("No movie ID found.")
                return np.NaN
    except Exception as e:
        print(f"An error occurred: {e}")
        return np.NaN

# Assuming df_2020 is your DataFrame and 'Title' is the column name
df_2020['genres'] = df_2020['Title'].map(lambda x: get_genre(str(x)))

Search result for 'The Grudge': {'page': 1, 'results': [{'adult': False, 'backdrop_path': '/e8nfiNRrcUfebNLPKtR6dzgV1M1.jpg', 'genre_ids': [27, 9648, 53], 'id': 1970, 'original_language': 'en', 'original_title': 'The Grudge', 'overview': 'An American nurse living and working in Tokyo is exposed to a mysterious supernatural curse, one that locks a person in a powerful rage before claiming their life and spreading to another victim.', 'popularity': 36.054, 'poster_path': '/5AGB8FVELnhMMw3nO372sw1xp58.jpg', 'release_date': '2004-10-22', 'title': 'The Grudge', 'video': False, 'vote_average': 5.902, 'vote_count': 2860}, {'adult': False, 'backdrop_path': '/iuW78LWxApCvjLuMebcICwF2owQ.jpg', 'genre_ids': [27, 9648], 'id': 465086, 'original_language': 'en', 'original_title': 'The Grudge', 'overview': 'After a young mother murders her family in her own house, a detective attempts to investigate the mysterious case, only to discover that the house is cursed by a vengeful ghost. Now targeted by th

API response for movie ID 1970: {'adult': False, 'backdrop_path': '/e8nfiNRrcUfebNLPKtR6dzgV1M1.jpg', 'belongs_to_collection': {'id': 1974, 'name': 'The Grudge Collection', 'poster_path': '/qQMAM4Kxioo9p95D4jOuGWN4Xjy.jpg', 'backdrop_path': '/w4HSdOMB2dTwZMZ0idNkAOvQMnK.jpg'}, 'budget': 10000000, 'genres': [{'id': 27, 'name': 'Horror'}, {'id': 9648, 'name': 'Mystery'}, {'id': 53, 'name': 'Thriller'}], 'homepage': '', 'id': 1970, 'imdb_id': 'tt0391198', 'origin_country': ['US'], 'original_language': 'en', 'original_title': 'The Grudge', 'overview': 'An American nurse living and working in Tokyo is exposed to a mysterious supernatural curse, one that locks a person in a powerful rage before claiming their life and spreading to another victim.', 'popularity': 36.054, 'poster_path': '/5AGB8FVELnhMMw3nO372sw1xp58.jpg', 'production_companies': [{'id': 768, 'logo_path': None, 'name': 'Ghost House Pictures', 'origin_country': 'US'}], 'production_countries': [{'iso_3166_1': 'US', 'name': 'Unite

Search result for 'Like a Boss': {'page': 1, 'results': [{'adult': False, 'backdrop_path': '/cH0AXST2dsHcD62qTbS4Cte6Wjb.jpg', 'genre_ids': [35], 'id': 526019, 'original_language': 'en', 'original_title': 'Like a Boss', 'overview': 'Two female friends with very different ideals decide to start a beauty company together. One is more practical, while the other wants to earn her fortune and live a lavish lifestyle.', 'popularity': 25.885, 'poster_path': '/yce0CZPWd0GGudksRJi8p4gDj1M.jpg', 'release_date': '2020-01-09', 'title': 'Like a Boss', 'video': False, 'vote_average': 6.293, 'vote_count': 621}, {'adult': False, 'backdrop_path': None, 'genre_ids': [28, 12], 'id': 859290, 'original_language': 'en', 'original_title': 'Like a Boss', 'overview': "A foolishly heroic guy gets himself into fights against thugs to save innocent people but gets beat up until his 'kick-ass' girlfriend comes to the rescue.", 'popularity': 1.045, 'poster_path': None, 'release_date': '2015-07-07', 'title': 'Like a

Search result for 'The Sonata': {'page': 1, 'results': [{'adult': False, 'backdrop_path': '/Klfe4c9DLMhhB648SuWDTkSGH6.jpg', 'genre_ids': [27, 53, 9648], 'id': 477036, 'original_language': 'en', 'original_title': 'The Sonata', 'overview': 'After a gifted musician inherits a mansion after her long lost father dies under mysterious circumstances, she discovers his last musical masterpiece riddled with cryptic symbols that unravels an evil secret, triggering dark forces that reach beyond her imagination.', 'popularity': 10.493, 'poster_path': '/iiL3AWKPx6GIZN6AmmSq7pbtyc.jpg', 'release_date': '2018-11-15', 'title': 'The Sonata', 'video': False, 'vote_average': 4.776, 'vote_count': 49}, {'adult': False, 'backdrop_path': None, 'genre_ids': [18], 'id': 926281, 'original_language': 'ja', 'original_title': '月光の夏', 'overview': 'Two soon-to-be kamikaze pilots stop by a local school near their base to play the piano one last time, leaving a deep impression on a teacher.  Years later, she seeks ou

API response for movie ID 527534: {'adult': False, 'backdrop_path': '/4iwHATla3Dc2jfFKfL8d0G6IHOp.jpg', 'belongs_to_collection': None, 'budget': 0, 'genres': [{'id': 53, 'name': 'Thriller'}, {'id': 18, 'name': 'Drama'}, {'id': 80, 'name': 'Crime'}], 'homepage': '', 'id': 527534, 'imdb_id': 'tt8415352', 'origin_country': ['US'], 'original_language': 'en', 'original_title': 'The Murder of Nicole Brown Simpson', 'overview': 'In 1994 Nicole Brown Simpson and her friend Ronald Goldman were brutally murdered in her Los Angeles home by whom most believe to be O.J Simpson. But what role did Glen Rogers, also known as the Casanova Killer play in their death?', 'popularity': 10.172, 'poster_path': '/pfTrRimCd5mDnb8qpTZovD5ZIsl.jpg', 'production_companies': [{'id': 117078, 'logo_path': '/hGoY5Bssr5aXeBmBrMCGUQFAp41.png', 'name': 'Skyline Entertainment', 'origin_country': 'US'}, {'id': 79050, 'logo_path': None, 'name': '1428 Films', 'origin_country': ''}, {'id': 116018, 'logo_path': None, 'name': 

...

API response for movie ID 508442: {'adult': False, 'backdrop_path': '/rQaHA74pevnGsxcKGaoZVGWe9TC.jpg', 'belongs_to_collection': None, 'budget': 150000000, 'genres': [{'id': 16, 'name': 'Animation'}, {'id': 10751, 'name': 'Family'}, {'id': 35, 'name': 'Comedy'}, {'id': 14, 'name': 'Fantasy'}], 'homepage': 'https://www.disneyplus.com/movies/soul/77zlWrb9vRYp', 'id': 508442, 'imdb_id': 'tt2948372', 'origin_country': ['US'], 'original_language': 'en', 'original_title': 'Soul', 'overview': 'Joe Gardner is a middle school teacher with a love for jazz music. After a successful audition at the Half Note Club, he suddenly gets into an accident that separates his soul from his body and is transported to the You Seminar, a center in which souls develop and gain passions before being transported to a newborn child. Joe must enlist help from the other souls-in-training, like 22, a soul who has spent eons in the You Seminar, in order to get back to Earth.', 'popularity': 100.814, 'poster_path': '/h

API response for movie ID 615677: {'adult': False, 'backdrop_path': '/y6FYAhaeFMj9Lsk8OdF2NeWQkbd.jpg', 'belongs_to_collection': {'id': 727089, 'name': 'Sharkboy and Lavagirl Collection', 'poster_path': '/9ygdf3deRFbQbZbwLxXuqM1rVwG.jpg', 'backdrop_path': '/2ztK0QFbUkOwe3TxAvqHjSJAFdB.jpg'}, 'budget': 0, 'genres': [{'id': 10751, 'name': 'Family'}, {'id': 28, 'name': 'Action'}, {'id': 14, 'name': 'Fantasy'}, {'id': 35, 'name': 'Comedy'}], 'homepage': 'https://www.netflix.com/title/80994666', 'id': 615677, 'imdb_id': 'tt10600398', 'origin_country': ['US'], 'original_language': 'en', 'original_title': 'We Can Be Heroes', 'overview': "When alien invaders capture Earth's superheroes, their kids must learn to work together to save their parents - and the planet.", 'popularity': 44.514, 'poster_path': '/1S21HpcKY6uQ9UAw68aICmrJaq6.jpg', 'production_companies': [{'id': 10807, 'logo_path': '/j0BcMaJKIiDDYHq9lriTcM0Npka.png', 'name': 'Troublemaker Studios', 'origin_country': 'US'}, {'id': 25608,

API response for movie ID 581032: {'adult': False, 'backdrop_path': '/oyBZyY5GdzZdofVVsDda49QmvFP.jpg', 'belongs_to_collection': None, 'budget': 38000000, 'genres': [{'id': 18, 'name': 'Drama'}, {'id': 37, 'name': 'Western'}, {'id': 12, 'name': 'Adventure'}], 'homepage': 'https://www.universalpictures.com/movies/news-of-the-world', 'id': 581032, 'imdb_id': 'tt6878306', 'origin_country': ['US'], 'original_language': 'en', 'original_title': 'News of the World', 'overview': 'A Texan traveling across the wild West bringing the news of the world to local townspeople, agrees to help rescue a young girl who was kidnapped.', 'popularity': 17.041, 'poster_path': '/fYQCgVRsQTEfUrP7cW5iAFVYOlh.jpg', 'production_companies': [{'id': 4171, 'logo_path': '/ip8rzankhLLhJGGkvfCirfUM26d.png', 'name': 'Playtone', 'origin_country': 'US'}, {'id': 8875, 'logo_path': None, 'name': 'Pretty Pictures', 'origin_country': 'US'}, {'id': 33, 'logo_path': '/8lvHyhjr8oUKOOy2dKXoALWKdp0.png', 'name': 'Universal Picture

API response for movie ID 641662: {'adult': False, 'backdrop_path': '/izNpxVcjKbF9BiYF4GVqxCOfewL.jpg', 'belongs_to_collection': None, 'budget': 0, 'genres': [{'id': 18, 'name': 'Drama'}], 'homepage': 'http://www.netflix.com/title/81128745', 'id': 641662, 'imdb_id': 'tt11161474', 'origin_country': ['CA', 'US'], 'original_language': 'en', 'original_title': 'Pieces of a Woman', 'overview': "When a young mother's home birth ends in unfathomable tragedy, she begins a year-long odyssey of mourning that fractures relationships with loved ones in this deeply personal story of a woman learning to live alongside her loss.", 'popularity': 17.667, 'poster_path': '/OgUfLlhfBFx5BPK6LzBWFvBW1w.jpg', 'production_companies': [{'id': 13240, 'logo_path': '/aTc07YaNHo8WNgkQSnvLmG6w4nW.png', 'name': 'Bron Studios', 'origin_country': 'CA'}, {'id': 126587, 'logo_path': None, 'name': 'Little Lamb Productions', 'origin_country': 'US'}, {'id': 17173, 'logo_path': '/ulj78XzGjDOiipXUCKUlJjKnZGf.png', 'name': 'Pr

c:\users\paras rana\appdata\local\programs\python\python37\lib\site-packages\ipykernel_launcher.py:35: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy


In [12]:
df_2020['genres'] = df_2020['Title'].map(lambda x: get_genre(str(x)))

Search result for 'The Grudge': {'page': 1, 'results': [{'adult': False, 'backdrop_path': '/e8nfiNRrcUfebNLPKtR6dzgV1M1.jpg', 'genre_ids': [27, 9648, 53], 'id': 1970, 'original_language': 'en', 'original_title': 'The Grudge', 'overview': 'An American nurse living and working in Tokyo is exposed to a mysterious supernatural curse, one that locks a person in a powerful rage before claiming their life and spreading to another victim.', 'popularity': 36.054, 'poster_path': '/5AGB8FVELnhMMw3nO372sw1xp58.jpg', 'release_date': '2004-10-22', 'title': 'The Grudge', 'video': False, 'vote_average': 5.902, 'vote_count': 2860}, {'adult': False, 'backdrop_path': '/iuW78LWxApCvjLuMebcICwF2owQ.jpg', 'genre_ids': [27, 9648], 'id': 465086, 'original_language': 'en', 'original_title': 'The Grudge', 'overview': 'After a young mother murders her family in her own house, a detective attempts to investigate the mysterious case, only to discover that the house is cursed by a vengeful ghost. Now targeted by th

API response for movie ID 526019: {'adult': False, 'backdrop_path': '/cH0AXST2dsHcD62qTbS4Cte6Wjb.jpg', 'belongs_to_collection': None, 'budget': 29000000, 'genres': [{'id': 35, 'name': 'Comedy'}], 'homepage': 'https://www.paramountmovies.com/movies/like-a-boss', 'id': 526019, 'imdb_id': 'tt7545266', 'origin_country': ['US'], 'original_language': 'en', 'original_title': 'Like a Boss', 'overview': 'Two female friends with very different ideals decide to start a beauty company together. One is more practical, while the other wants to earn her fortune and live a lavish lifestyle.', 'popularity': 25.885, 'poster_path': '/yce0CZPWd0GGudksRJi8p4gDj1M.jpg', 'production_companies': [{'id': 106497, 'logo_path': '/l7nrRW41bLB1M6wK6sDDpxvDQBp.png', 'name': 'Artists First', 'origin_country': 'US'}, {'id': 4, 'logo_path': '/gz66EfNoYPqHTYI4q9UEN4CbHRc.png', 'name': 'Paramount Pictures', 'origin_country': 'US'}], 'production_countries': [{'iso_3166_1': 'US', 'name': 'United States of America'}], 'rel

API response for movie ID 477036: {'adult': False, 'backdrop_path': '/Klfe4c9DLMhhB648SuWDTkSGH6.jpg', 'belongs_to_collection': None, 'budget': 0, 'genres': [{'id': 27, 'name': 'Horror'}, {'id': 53, 'name': 'Thriller'}, {'id': 9648, 'name': 'Mystery'}], 'homepage': '', 'id': 477036, 'imdb_id': 'tt7149066', 'origin_country': ['US', 'GB'], 'original_language': 'en', 'original_title': 'The Sonata', 'overview': 'After a gifted musician inherits a mansion after her long lost father dies under mysterious circumstances, she discovers his last musical masterpiece riddled with cryptic symbols that unravels an evil secret, triggering dark forces that reach beyond her imagination.', 'popularity': 10.493, 'poster_path': '/iiL3AWKPx6GIZN6AmmSq7pbtyc.jpg', 'production_companies': [{'id': 318, 'logo_path': '/q0UG4oZERwIywJdDPF4lRlvdYGW.png', 'name': 'CTB Film Company', 'origin_country': 'RU'}, {'id': 93635, 'logo_path': '/pLoHlno5S4gKUNo4FuRG8bLdaYJ.png', 'name': 'Tasse Film', 'origin_country': 'LV'}

API response for movie ID 38700: {'adult': False, 'backdrop_path': '/eAIHqfS3kXm7kZl4j7ZBfdegyEz.jpg', 'belongs_to_collection': {'id': 14890, 'name': 'Bad Boys Collection', 'poster_path': '/iB59poJBofg1ciKlu6LzZakf11m.jpg', 'backdrop_path': '/k9hhSHg5GS4UgWQC6MHBOZrarji.jpg'}, 'budget': 90000000, 'genres': [{'id': 53, 'name': 'Thriller'}, {'id': 28, 'name': 'Action'}, {'id': 80, 'name': 'Crime'}], 'homepage': 'https://www.sonypictures.com/movies/badboysforlife', 'id': 38700, 'imdb_id': 'tt1502397', 'origin_country': ['US'], 'original_language': 'en', 'original_title': 'Bad Boys for Life', 'overview': 'Marcus and Mike are forced to confront new threats, career changes, and midlife crises as they join the newly created elite team AMMO of the Miami police department to take down the ruthless Armando Armas, the vicious leader of a Miami drug cartel.', 'popularity': 327.603, 'poster_path': '/y95lQLnuNKdPAzw9F9Ab8kJ80c3.jpg', 'production_companies': [{'id': 5, 'logo_path': '/71BqEFAF4V3qjjMP

API response for movie ID 522627: {'adult': False, 'backdrop_path': '/tintsaQ0WLzZsTMkTiqtMB3rfc8.jpg', 'belongs_to_collection': None, 'budget': 22000000, 'genres': [{'id': 28, 'name': 'Action'}, {'id': 80, 'name': 'Crime'}, {'id': 35, 'name': 'Comedy'}], 'homepage': 'https://www.miramax.com/movie/the-gentlemen', 'id': 522627, 'imdb_id': 'tt8367814', 'origin_country': ['GB'], 'original_language': 'en', 'original_title': 'The Gentlemen', 'overview': 'American expat Mickey Pearson has built a highly profitable marijuana empire in London. When word gets out that he’s looking to cash out of the business forever it triggers plots, schemes, bribery and blackmail in an attempt to steal his domain out from under him.', 'popularity': 61.531, 'poster_path': '/jtrhTYB7xSrJxR1vusu99nvnZ1g.jpg', 'production_companies': [{'id': 14, 'logo_path': '/m6AHu84oZQxvq7n1rsvMNJIAsMu.png', 'name': 'Miramax', 'origin_country': 'US'}, {'id': 2900, 'logo_path': None, 'name': 'Toff Guy Films', 'origin_country': '

...

API response for movie ID 549514: {'adult': False, 'backdrop_path': '/tljkeU2y1dCvT51Sv4ciNf0VfmV.jpg', 'belongs_to_collection': None, 'budget': 0, 'genres': [{'id': 18, 'name': 'Drama'}, {'id': 53, 'name': 'Thriller'}], 'homepage': 'https://fatale.movie', 'id': 549514, 'imdb_id': 'tt8829830', 'origin_country': ['US'], 'original_language': 'en', 'original_title': 'Fatale', 'overview': "After a one-night stand, a successful married man finds himself entangled and tricked in a female detective's latest investigation murder scheme.", 'popularity': 32.137, 'poster_path': '/tGFXEyESXIuei5tZWXRkSRSFSxi.jpg', 'production_companies': [{'id': 102809, 'logo_path': '/5hoxf5oxUF56UWqWbIt2BjWmZ6m.png', 'name': 'Hidden Empire Film Group', 'origin_country': 'US'}, {'id': 491, 'logo_path': '/5LvDUt3KmvRnXQ4NrdWJYHeuA8J.png', 'name': 'Summit Entertainment', 'origin_country': 'US'}], 'production_countries': [{'iso_3166_1': 'US', 'name': 'United States of America'}], 'release_date': '2020-12-18', 'revenu

API response for movie ID 651571: {'adult': False, 'backdrop_path': '/nz8xWrTKZzA5A7FgxaM4kfAoO1W.jpg', 'belongs_to_collection': None, 'budget': 0, 'genres': [{'id': 878, 'name': 'Science Fiction'}, {'id': 28, 'name': 'Action'}, {'id': 27, 'name': 'Horror'}], 'homepage': '', 'id': 651571, 'imdb_id': 'tt9820556', 'origin_country': ['CA', 'US'], 'original_language': 'en', 'original_title': 'Breach', 'overview': 'A hardened mechanic must stay awake and maintain an interstellar ark fleeing the dying planet Earth with a few thousand lucky souls on board... the last of humanity. Unfortunately, humans are not the only passengers. A shapeshifting alien creature has taken residence, its only goal is to kill as many people as possible. The crew must think quickly to stop this menace before it destroys mankind.', 'popularity': 46.318, 'poster_path': '/13B6onhL6FzSN2KaNeQeMML05pS.jpg', 'production_companies': [{'id': 68628, 'logo_path': '/ez4m0Hw5puaHjNvGEcf6YbFaaNL.png', 'name': '308 Enterprises'

API response for movie ID 581032: {'adult': False, 'backdrop_path': '/oyBZyY5GdzZdofVVsDda49QmvFP.jpg', 'belongs_to_collection': None, 'budget': 38000000, 'genres': [{'id': 18, 'name': 'Drama'}, {'id': 37, 'name': 'Western'}, {'id': 12, 'name': 'Adventure'}], 'homepage': 'https://www.universalpictures.com/movies/news-of-the-world', 'id': 581032, 'imdb_id': 'tt6878306', 'origin_country': ['US'], 'original_language': 'en', 'original_title': 'News of the World', 'overview': 'A Texan traveling across the wild West bringing the news of the world to local townspeople, agrees to help rescue a young girl who was kidnapped.', 'popularity': 17.041, 'poster_path': '/fYQCgVRsQTEfUrP7cW5iAFVYOlh.jpg', 'production_companies': [{'id': 4171, 'logo_path': '/ip8rzankhLLhJGGkvfCirfUM26d.png', 'name': 'Playtone', 'origin_country': 'US'}, {'id': 8875, 'logo_path': None, 'name': 'Pretty Pictures', 'origin_country': 'US'}, {'id': 33, 'logo_path': '/8lvHyhjr8oUKOOy2dKXoALWKdp0.png', 'name': 'Universal Picture

API response for movie ID 641662: {'adult': False, 'backdrop_path': '/izNpxVcjKbF9BiYF4GVqxCOfewL.jpg', 'belongs_to_collection': None, 'budget': 0, 'genres': [{'id': 18, 'name': 'Drama'}], 'homepage': 'http://www.netflix.com/title/81128745', 'id': 641662, 'imdb_id': 'tt11161474', 'origin_country': ['CA', 'US'], 'original_language': 'en', 'original_title': 'Pieces of a Woman', 'overview': "When a young mother's home birth ends in unfathomable tragedy, she begins a year-long odyssey of mourning that fractures relationships with loved ones in this deeply personal story of a woman learning to live alongside her loss.", 'popularity': 17.667, 'poster_path': '/OgUfLlhfBFx5BPK6LzBWFvBW1w.jpg', 'production_companies': [{'id': 13240, 'logo_path': '/aTc07YaNHo8WNgkQSnvLmG6w4nW.png', 'name': 'Bron Studios', 'origin_country': 'CA'}, {'id': 126587, 'logo_path': None, 'name': 'Little Lamb Productions', 'origin_country': 'US'}, {'id': 17173, 'logo_path': '/ulj78XzGjDOiipXUCKUlJjKnZGf.png', 'name': 'Pr

c:\users\paras rana\appdata\local\programs\python\python37\lib\site-packages\ipykernel_launcher.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  """Entry point for launching an IPython kernel.


In [13]:
df_2020

Title                                      Cast and crew  \
0               The Grudge  Nicolas Pesce (director/screenplay); Andrea Ri...   
1               Underwater  William Eubank (director); Brian Duffield, Ada...   
2              Like a Boss  Miguel Arteta (director); Sam Pitman, Adam Col...   
3            Three Christs  Jon Avnet (director/screenplay); Eric Nazarian...   
4        Inherit the Viper  Anthony Jerjen (director); Andrew Crabtree (sc...   
..                     ...                                                ...   
270       We Can Be Heroes  Robert Rodriguez (director/screenplay); Priyan...   
271      News of the World  Paul Greengrass (director/screenplay); Luke Da...   
272  One Night in Miami...  Regina King (director); Kemp Powers (screenpla...   
273  Promising Young Woman  Emerald Fennell (director/screenplay); Carey M...   
274      Pieces of a Woman  Kornél Mundruczó (director); Kata Wéber (scree...   

                                      genres  
0                    Horror Mystery Thriller  
1    Horror Science Fiction Action Adventure  
2                                     Comedy  
3                                      Drama  
4                       Crime Thriller Drama  
..                                       ...  
270             Family Action Fantasy Comedy  
271                  Drama Western Adventure  
272                                    Drama  
273                     Thriller Crime Drama  
274                                    Drama  

[275 rows x 3 columns]

In [14]:
df_2020.isna().sum()

Title            0
Cast and crew    0
genres           2
dtype: int64

In [15]:
def get_director(x):
    if " (director)" in x:
        return x.split(" (director)")[0]
    elif " (directors)" in x:
        return x.split(" (directors)")[0]
    else:
        return x.split(" (director/screenplay)")[0]

In [16]:
df_2020['director_name'] = df_2020['Cast and crew'].map(lambda x: get_director(x))

c:\users\paras rana\appdata\local\programs\python\python37\lib\site-packages\ipykernel_launcher.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  """Entry point for launching an IPython kernel.


In [17]:
def get_actor1(x):
    return ((x.split("screenplay); ")[-1]).split(", ")[0])

In [18]:
df_2020['actor_1_name'] = df['Cast and crew'].map(lambda x: get_actor1(x))

c:\users\paras rana\appdata\local\programs\python\python37\lib\site-packages\ipykernel_launcher.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  """Entry point for launching an IPython kernel.


In [19]:
def get_actor2(x):
    if len((x.split("screenplay); ")[-1]).split(", ")) < 2:
        return np.NaN
    else:
        return ((x.split("screenplay); ")[-1]).split(", ")[1])

In [20]:
df_2020['actor_2_name'] = df_2020['Cast and crew'].map(lambda x: get_actor2(x))

c:\users\paras rana\appdata\local\programs\python\python37\lib\site-packages\ipykernel_launcher.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  """Entry point for launching an IPython kernel.


In [21]:
def get_actor3(x):
    if len((x.split("screenplay); ")[-1]).split(", ")) < 3:
        return np.NaN
    else:
        return ((x.split("screenplay); ")[-1]).split(", ")[2])

In [22]:
df_2020['actor_3_name'] = df_2020['Cast and crew'].map(lambda x: get_actor3(x))

In [23]:
df_2020

Title                                      Cast and crew  \
0               The Grudge  Nicolas Pesce (director/screenplay); Andrea Ri...   
1               Underwater  William Eubank (director); Brian Duffield, Ada...   
2              Like a Boss  Miguel Arteta (director); Sam Pitman, Adam Col...   
3            Three Christs  Jon Avnet (director/screenplay); Eric Nazarian...   
4        Inherit the Viper  Anthony Jerjen (director); Andrew Crabtree (sc...   
..                     ...                                                ...   
270       We Can Be Heroes  Robert Rodriguez (director/screenplay); Priyan...   
271      News of the World  Paul Greengrass (director/screenplay); Luke Da...   
272  One Night in Miami...  Regina King (director); Kemp Powers (screenpla...   
273  Promising Young Woman  Emerald Fennell (director/screenplay); Carey M...   
274      Pieces of a Woman  Kornél Mundruczó (director); Kata Wéber (scree...   

                                      genres     director_name  \
0                    Horror Mystery Thriller     Nicolas Pesce   
1    Horror Science Fiction Action Adventure    William Eubank   
2                                     Comedy     Miguel Arteta   
3                                      Drama         Jon Avnet   
4                       Crime Thriller Drama    Anthony Jerjen   
..                                       ...               ...   
270             Family Action Fantasy Comedy  Robert Rodriguez   
271                  Drama Western Adventure   Paul Greengrass   
272                                    Drama       Regina King   
273                     Thriller Crime Drama   Emerald Fennell   
274                                    Drama  Kornél Mundruczó   

              actor_1_name       actor_2_name     actor_3_name  
0       Andrea Riseborough      Demián Bichir         John Cho  
1          Kristen Stewart     Vincent Cassel  Jessica Henwick  
2          Tiffany Haddish         Rose Byrne      Salma Hayek  
3             Richard Gere     Peter Dinklage   Walton Goggins  
4            Josh Hartnett  Margarita Levieva   Chandler Riggs  
..                     ...                ...              ...  
270  Priyanka Chopra Jonas       Pedro Pascal    YaYa Gosselin  
271              Tom Hanks      Helena Zengel              NaN  
272      Kingsley Ben-Adir          Eli Goree      Aldis Hodge  
273         Carey Mulligan         Bo Burnham      Alison Brie  
274          Vanessa Kirby       Shia LaBeouf     Molly Parker  

[275 rows x 7 columns]

In [24]:
df_2020 = df_2020.rename(columns = {'Title':'movie_title'})

In [25]:
newdf_2020 = df_2020.loc[: , ['director_name' , 'actor_1_name' , 'actor_2_name' , 'actor_3_name' , 'genres' , 'movie_title']]

In [26]:
newdf_2020

director_name           actor_1_name       actor_2_name  \
0       Nicolas Pesce     Andrea Riseborough      Demián Bichir   
1      William Eubank        Kristen Stewart     Vincent Cassel   
2       Miguel Arteta        Tiffany Haddish         Rose Byrne   
3           Jon Avnet           Richard Gere     Peter Dinklage   
4      Anthony Jerjen          Josh Hartnett  Margarita Levieva   
..                ...                    ...                ...   
270  Robert Rodriguez  Priyanka Chopra Jonas       Pedro Pascal   
271   Paul Greengrass              Tom Hanks      Helena Zengel   
272       Regina King      Kingsley Ben-Adir          Eli Goree   
273   Emerald Fennell         Carey Mulligan         Bo Burnham   
274  Kornél Mundruczó          Vanessa Kirby       Shia LaBeouf   

        actor_3_name                                   genres  \
0           John Cho                  Horror Mystery Thriller   
1    Jessica Henwick  Horror Science Fiction Action Adventure   
2        Salma Hayek                                   Comedy   
3     Walton Goggins                                    Drama   
4     Chandler Riggs                     Crime Thriller Drama   
..               ...                                      ...   
270    YaYa Gosselin             Family Action Fantasy Comedy   
271              NaN                  Drama Western Adventure   
272      Aldis Hodge                                    Drama   
273      Alison Brie                     Thriller Crime Drama   
274     Molly Parker                                    Drama   

               movie_title  
0               The Grudge  
1               Underwater  
2              Like a Boss  
3            Three Christs  
4        Inherit the Viper  
..                     ...  
270       We Can Be Heroes  
271      News of the World  
272  One Night in Miami...  
273  Promising Young Woman  
274      Pieces of a Woman  

[275 rows x 6 columns]

In [27]:
newdf_2020['comb'] = newdf_2020['actor_1_name'] + ' ' + newdf_2020['actor_2_name'] + ' ' + newdf_2020['actor_3_name'] + ' ' + newdf_2020['director_name'] + ' ' + newdf_2020['genres']

In [28]:
newdf_2020

director_name           actor_1_name       actor_2_name  \
0       Nicolas Pesce     Andrea Riseborough      Demián Bichir   
1      William Eubank        Kristen Stewart     Vincent Cassel   
2       Miguel Arteta        Tiffany Haddish         Rose Byrne   
3           Jon Avnet           Richard Gere     Peter Dinklage   
4      Anthony Jerjen          Josh Hartnett  Margarita Levieva   
..                ...                    ...                ...   
270  Robert Rodriguez  Priyanka Chopra Jonas       Pedro Pascal   
271   Paul Greengrass              Tom Hanks      Helena Zengel   
272       Regina King      Kingsley Ben-Adir          Eli Goree   
273   Emerald Fennell         Carey Mulligan         Bo Burnham   
274  Kornél Mundruczó          Vanessa Kirby       Shia LaBeouf   

        actor_3_name                                   genres  \
0           John Cho                  Horror Mystery Thriller   
1    Jessica Henwick  Horror Science Fiction Action Adventure   
2        Salma Hayek                                   Comedy   
3     Walton Goggins                                    Drama   
4     Chandler Riggs                     Crime Thriller Drama   
..               ...                                      ...   
270    YaYa Gosselin             Family Action Fantasy Comedy   
271              NaN                  Drama Western Adventure   
272      Aldis Hodge                                    Drama   
273      Alison Brie                     Thriller Crime Drama   
274     Molly Parker                                    Drama   

               movie_title                                               comb  
0               The Grudge  Andrea Riseborough Demián Bichir John Cho Nico...  
1               Underwater  Kristen Stewart Vincent Cassel Jessica Henwick...  
2              Like a Boss  Tiffany Haddish Rose Byrne Salma Hayek Miguel ...  
3            Three Christs  Richard Gere Peter Dinklage Walton Goggins Jon...  
4        Inherit the Viper  Josh Hartnett Margarita Levieva Chandler Riggs...  
..                     ...                                                ...  
270       We Can Be Heroes  Priyanka Chopra Jonas Pedro Pascal YaYa Gossel...  
271      News of the World                                                NaN  
272  One Night in Miami...  Kingsley Ben-Adir Eli Goree Aldis Hodge Regina...  
273  Promising Young Woman  Carey Mulligan Bo Burnham Alison Brie Emerald ...  
274      Pieces of a Woman  Vanessa Kirby Shia LaBeouf Molly Parker Kornél...  

[275 rows x 7 columns]

In [29]:
newdf_2020['movie_title'] = newdf_2020['movie_title'].str.lower()

In [30]:
newdf_2020.isna().sum()

director_name     0
actor_1_name      0
actor_2_name      5
actor_3_name     28
genres            2
movie_title       0
comb             29
dtype: int64

In [31]:
newdf_2020 = newdf_2020.dropna(how='any')

In [32]:
newdf_2020.isna().sum()

director_name    0
actor_1_name     0
actor_2_name     0
actor_3_name     0
genres           0
movie_title      0
comb             0
dtype: int64

In [33]:
newdf_2020

director_name           actor_1_name       actor_2_name  \
0       Nicolas Pesce     Andrea Riseborough      Demián Bichir   
1      William Eubank        Kristen Stewart     Vincent Cassel   
2       Miguel Arteta        Tiffany Haddish         Rose Byrne   
3           Jon Avnet           Richard Gere     Peter Dinklage   
4      Anthony Jerjen          Josh Hartnett  Margarita Levieva   
..                ...                    ...                ...   
269       Pete Docter             Jamie Foxx           Tina Fey   
270  Robert Rodriguez  Priyanka Chopra Jonas       Pedro Pascal   
272       Regina King      Kingsley Ben-Adir          Eli Goree   
273   Emerald Fennell         Carey Mulligan         Bo Burnham   
274  Kornél Mundruczó          Vanessa Kirby       Shia LaBeouf   

        actor_3_name                                   genres  \
0           John Cho                  Horror Mystery Thriller   
1    Jessica Henwick  Horror Science Fiction Action Adventure   
2        Salma Hayek                                   Comedy   
3     Walton Goggins                                    Drama   
4     Chandler Riggs                     Crime Thriller Drama   
..               ...                                      ...   
269    Graham Norton          Animation Family Comedy Fantasy   
270    YaYa Gosselin             Family Action Fantasy Comedy   
272      Aldis Hodge                                    Drama   
273      Alison Brie                     Thriller Crime Drama   
274     Molly Parker                                    Drama   

               movie_title                                               comb  
0               the grudge  Andrea Riseborough Demián Bichir John Cho Nico...  
1               underwater  Kristen Stewart Vincent Cassel Jessica Henwick...  
2              like a boss  Tiffany Haddish Rose Byrne Salma Hayek Miguel ...  
3            three christs  Richard Gere Peter Dinklage Walton Goggins Jon...  
4        inherit the viper  Josh Hartnett Margarita Levieva Chandler Riggs...  
..                     ...                                                ...  
269                   soul  Jamie Foxx Tina Fey Graham Norton Pete Docter ...  
270       we can be heroes  Priyanka Chopra Jonas Pedro Pascal YaYa Gossel...  
272  one night in miami...  Kingsley Ben-Adir Eli Goree Aldis Hodge Regina...  
273  promising young woman  Carey Mulligan Bo Burnham Alison Brie Emerald ...  
274      pieces of a woman  Vanessa Kirby Shia LaBeouf Molly Parker Kornél...  

[246 rows x 7 columns]

### Extracting featues of the 2021 Movies from Wikipedia

In [34]:
link = 'https://en.wikipedia.org/wiki/List_of_American_films_of_2021'

In [35]:
source = urllib.request.urlopen(link).read()
soup = bs.BeautifulSoup(source , 'lxml')

In [36]:
tables = soup.find_all('table' , class_='wikitable sortable')

In [37]:
df1 = pd.read_html(str(tables[0]))[0]
df2 = pd.read_html(str(tables[1]))[0]
df3 = pd.read_html(str(tables[2]))[0]
df4 = pd.read_html(str(tables[3]).replace("'1\"\'",'"1"'))[0] # avoided "ValueError: invalid literal for int() with base 10: '1"'

In [38]:
df = df1.append(df2.append(df3.append(df4 , ignore_index=True) , ignore_index=True) , ignore_index=True)

In [39]:
df

Opening  Opening.1                            Title  \
0     JANUARY        1.0              Shadow in the Cloud   
1     JANUARY        5.0                          Hacksaw   
2     JANUARY       12.0  Dr. Bird's Advice for Sad Poets   
3     JANUARY       13.0                  The White Tiger   
4     JANUARY       14.0                      Locked Down   
..        ...        ...                              ...   
360  DECEMBER       25.0           The Tragedy of Macbeth   
361  DECEMBER       25.0             A Journal for Jordan   
362  DECEMBER       25.0                American Underdog   
363  DECEMBER       26.0                          Memoria   
364  DECEMBER        NaN                              NaN   

                                    Production company  \
0                               Vertical Entertainment   
1                     Leone Films / Midnight Releasing   
2             Relativity Media / Ketchup Entertainment   
3             Netflix / ARRAY / Purple Pebble Pictures   
4                      HBO Max / Warner Bros. Pictures   
..                                                 ...   
360                        Apple TV+ / A24 / IAC Films   
361  Columbia Pictures / Escape Artists / Bron Studios   
362                                          Lionsgate   
363                                               Neon   
364                                                NaN   

                                         Cast and crew  \
0    Roseanne Liang (director/screenplay); Max Land...   
1    Anthony Leone (director/screenplay); Amy Cay, ...   
2    Yaniv Raz (director/screenplay); Lucas Jade Zu...   
3    Ramin Bahrani (director/screenplay); Adarsh Go...   
4    Doug Liman (director); Steven Knight (screenpl...   
..                                                 ...   
360  Joel Coen (director/screenplay); Denzel Washin...   
361  Denzel Washington (director); Virgil Williams ...   
362  Erwin brothers (directors); Jon Erwin, David A...   
363  Apichatpong Weerasethakul (director/acreenplay...   
364                                                NaN   

    .mw-parser-output .tooltip-dotted{border-bottom:1px dotted;cursor:help}Ref.  \
0                                                  [2]                            
1                                                  [3]                            
2                                                  [4]                            
3                                                  NaN                            
4                                                  [5]                            
..                                                 ...                            
360                                                NaN                            
361                                                NaN                            
362                                                NaN                            
363                                                NaN                            
364                                                NaN                            

      Ref.  
0      NaN  
1      NaN  
2      NaN  
3      NaN  
4      NaN  
..     ...  
360  [277]  
361  [278]  
362  [279]  
363  [280]  
364    NaN  

[365 rows x 7 columns]

In [40]:
df_2021 = df[['Title' , 'Cast and crew']]

In [41]:
df_2021

Title  \
0                Shadow in the Cloud   
1                            Hacksaw   
2    Dr. Bird's Advice for Sad Poets   
3                    The White Tiger   
4                        Locked Down   
..                               ...   
360           The Tragedy of Macbeth   
361             A Journal for Jordan   
362                American Underdog   
363                          Memoria   
364                              NaN   

                                         Cast and crew  
0    Roseanne Liang (director/screenplay); Max Land...  
1    Anthony Leone (director/screenplay); Amy Cay, ...  
2    Yaniv Raz (director/screenplay); Lucas Jade Zu...  
3    Ramin Bahrani (director/screenplay); Adarsh Go...  
4    Doug Liman (director); Steven Knight (screenpl...  
..                                                 ...  
360  Joel Coen (director/screenplay); Denzel Washin...  
361  Denzel Washington (director); Virgil Williams ...  
362  Erwin brothers (directors); Jon Erwin, David A...  
363  Apichatpong Weerasethakul (director/acreenplay...  
364                                                NaN  

[365 rows x 2 columns]

In [42]:
df_2021.isna().sum()

Title            1
Cast and crew    1
dtype: int64

In [43]:
df_2021 = df_2021.dropna(how='any')

In [44]:
df_2021

Title  \
0                Shadow in the Cloud   
1                            Hacksaw   
2    Dr. Bird's Advice for Sad Poets   
3                    The White Tiger   
4                        Locked Down   
..                               ...   
359                   The King's Man   
360           The Tragedy of Macbeth   
361             A Journal for Jordan   
362                American Underdog   
363                          Memoria   

                                         Cast and crew  
0    Roseanne Liang (director/screenplay); Max Land...  
1    Anthony Leone (director/screenplay); Amy Cay, ...  
2    Yaniv Raz (director/screenplay); Lucas Jade Zu...  
3    Ramin Bahrani (director/screenplay); Adarsh Go...  
4    Doug Liman (director); Steven Knight (screenpl...  
..                                                 ...  
359  Matthew Vaughn (director/screenplay); Karl Gaj...  
360  Joel Coen (director/screenplay); Denzel Washin...  
361  Denzel Washington (director); Virgil Williams ...  
362  Erwin brothers (directors); Jon Erwin, David A...  
363  Apichatpong Weerasethakul (director/acreenplay...  

[364 rows x 2 columns]

In [45]:
df_2021.isna().sum()

Title            0
Cast and crew    0
dtype: int64

In [46]:
def get_genre(x):
    genres = []
    try:
        result = tmdb_movie.search(x)
        print(f"Search result for '{x}': {result}")  # Debug print
        if not result:
            print("No results found.")
            return np.NaN
        else:
            movie = result[0]
            print(f"First movie in result: {movie}")  # Debug print
            movie_id = getattr(movie, 'id', None)
            if movie_id:
                response = requests.get(f'https://api.themoviedb.org/3/movie/{movie_id}?api_key={tmdb.api_key}')
                data_json = response.json()
                print(f"API response for movie ID {movie_id}: {data_json}")  # Debug print
                if 'genres' in data_json and data_json['genres']:
                    genre_str = " "
                    for genre in data_json['genres']:
                        genres.append(genre['name'])
                    return genre_str.join(genres)
                else:
                    print("No genres found in movie data.")
                    return np.NaN
            else:
                print("No movie ID found.")
                return np.NaN
    except Exception as e:
        print(f"An error occurred: {e}")
        return np.NaN

# Assuming df_2020 is your DataFrame and 'Title' is the column name
df_2021['genres'] = df_2021['Title'].map(lambda x: get_genre(str(x)))

Search result for 'Shadow in the Cloud': {'page': 1, 'results': [{'adult': False, 'backdrop_path': '/aHYUj0hICtWZ5tPiCIm6pWUcjYK.jpg', 'genre_ids': [27, 28, 10752], 'id': 675327, 'original_language': 'en', 'original_title': 'Shadow in the Cloud', 'overview': 'A WWII pilot traveling with top secret documents on a B-17 Flying Fortress encounters an evil presence on board the flight.', 'popularity': 27.772, 'poster_path': '/t7EUMSlfUN3jUSZUJOLURAzJzZs.jpg', 'release_date': '2020-12-31', 'title': 'Shadow in the Cloud', 'video': False, 'vote_average': 5.835, 'vote_count': 936}, {'adult': False, 'backdrop_path': '/xZCAlWx5NRc9qxBLQba4jSHWLM4.jpg', 'genre_ids': [18], 'id': 1268743, 'original_language': 'es', 'original_title': 'Cuando las nubes esconden la sombra', 'overview': "Maria travels to Puerto Williams to star in a movie. But the film crew won't be able to arrive due to a strong storm. Alone, she'll seek help for severe back pain, which will lead her to discover life in the southernmos

API response for movie ID 275506: {'adult': False, 'backdrop_path': '/otgkht9XAdFnaOwttLqZoyvagXH.jpg', 'belongs_to_collection': None, 'budget': 0, 'genres': [{'id': 12, 'name': 'Adventure'}, {'id': 10751, 'name': 'Family'}, {'id': 10770, 'name': 'TV Movie'}, {'id': 37, 'name': 'Western'}], 'homepage': '', 'id': 275506, 'imdb_id': 'tt0067172', 'origin_country': ['US'], 'original_language': 'en', 'original_title': 'Hacksaw', 'overview': "A girl goes on vacation to the mountains where she finds a wild horse named Hacksaw. With a little help, she captures the stud and it doesn't take long until the man who helped her starts wagon racing, since Hacksaw refuses to have any man or woman on his back.", 'popularity': 2.708, 'poster_path': '/ajE4vD4eFDmCEcSe2KxO9aXV1gt.jpg', 'production_companies': [{'id': 3166, 'logo_path': '/vyyv4Gy9nPqAZKElPm2izLlEaVS.png', 'name': 'Walt Disney Productions', 'origin_country': 'US'}], 'production_countries': [{'iso_3166_1': 'US', 'name': 'United States of Ame

API response for movie ID 628534: {'adult': False, 'backdrop_path': '/wmx5vrNH6GEpv4NLACfibZlA1bq.jpg', 'belongs_to_collection': None, 'budget': 0, 'genres': [{'id': 18, 'name': 'Drama'}], 'homepage': 'https://www.netflix.com/title/80202877', 'id': 628534, 'imdb_id': 'tt6571548', 'origin_country': ['SG', 'US'], 'original_language': 'en', 'original_title': 'The White Tiger', 'overview': 'An ambitious Indian driver uses his wit and cunning to escape from poverty and rise to the top. An epic journey based on the New York Times bestseller.', 'popularity': 16.424, 'poster_path': '/5JnmseS3DZ6ad2VMbrnbGCs8Rst.jpg', 'production_companies': [{'id': 144369, 'logo_path': None, 'name': 'Lava Media', 'origin_country': 'SG'}, {'id': 10944, 'logo_path': None, 'name': 'Noruz Films', 'origin_country': 'US'}, {'id': 138297, 'logo_path': '/pQYDFhK4SFg20XRiK86qitJt4i6.png', 'name': 'ARRAY Filmworks', 'origin_country': 'US'}], 'production_countries': [{'iso_3166_1': 'IN', 'name': 'India'}, {'iso_3166_1': 

Search result for 'The Dig': {'page': 1, 'results': [{'adult': False, 'backdrop_path': '/wQhe2YJnB9AAS08RqwMeKN2ywUr.jpg', 'genre_ids': [18, 36], 'id': 532865, 'original_language': 'en', 'original_title': 'The Dig', 'overview': "As WWII looms, a wealthy widow hires an amateur archaeologist to excavate the burial mounds on her estate. When they make a historic discovery, the echoes of Britain's past resonate in the face of its uncertain future\u200e.", 'popularity': 26.98, 'poster_path': '/dFDNb9Gk1kyLRcconpj7Mc7C7IL.jpg', 'release_date': '2021-01-14', 'title': 'The Dig', 'video': False, 'vote_average': 6.87, 'vote_count': 1150}, {'adult': False, 'backdrop_path': '/ndyYuqQ0LbqCVo2JKYiG8gD4ppJ.jpg', 'genre_ids': [53], 'id': 519316, 'original_language': 'en', 'original_title': 'The Dig', 'overview': 'After serving fifteen years for murder, Callahan returns home to find Sean, his victim’s father, searching for the body. With no memory of the murder, Callahan soon realises that the only way

Search result for 'Outside the Wire': {'page': 1, 'results': [{'adult': False, 'backdrop_path': '/lOSdUkGQmbAl5JQ3QoHqBZUbZhC.jpg', 'genre_ids': [53, 28, 878], 'id': 775996, 'original_language': 'en', 'original_title': 'Outside the Wire', 'overview': 'In the near future, a drone pilot is sent into a deadly militarized zone and must work with an android officer to locate a doomsday device.', 'popularity': 29.871, 'poster_path': '/6XYLiMxHAaCsoyrVo38LBWMw2p8.jpg', 'release_date': '2021-01-15', 'title': 'Outside the Wire', 'video': False, 'vote_average': 6.363, 'vote_count': 1757}, {'adult': False, 'backdrop_path': None, 'genre_ids': [10752, 18], 'id': 787742, 'original_language': 'en', 'original_title': 'Outside the Wire', 'overview': 'A female Australian soldier cut off from her team, lies trapped in a collapsed building behind enemy lines. With a broken leg and minimal supplies, she is on her own until the unlikely arrival of a frightened 10 year old boy wielding a rifle, who helps her

...

API response for movie ID 826749: {'adult': False, 'backdrop_path': '/yxEaXRxFJqSmL0oXswDSBInBeIM.jpg', 'belongs_to_collection': {'id': 883509, 'name': 'Fortress (2021) Collection', 'poster_path': '/mE4e7Xeh6Kv9w1y0jHxG3FVvBR4.jpg', 'backdrop_path': '/jXZyPIC2ok9mshZEQOd0I9ZNG9N.jpg'}, 'budget': 20000000, 'genres': [{'id': 28, 'name': 'Action'}, {'id': 53, 'name': 'Thriller'}, {'id': 80, 'name': 'Crime'}], 'homepage': '', 'id': 826749, 'imdb_id': 'tt14577300', 'origin_country': ['US'], 'original_language': 'en', 'original_title': 'Fortress', 'overview': 'The story revolves around a top-secret resort for retired U.S. intelligence officers. A group of criminals led by Balzary breach the compound, hellbent on revenge on Robert, forcing the retired officer and his son to save the day.', 'popularity': 22.508, 'poster_path': '/vPadBKOdzKIk8mKTs4qDmdY8TLJ.jpg', 'production_companies': [{'id': 10405, 'logo_path': None, 'name': 'EFO Films', 'origin_country': 'US'}, {'id': 3604, 'logo_path': '/j

API response for movie ID 438695: {'adult': False, 'backdrop_path': '/6mJrgL7Mi13XjJeGYJFlD6UEVQw.jpg', 'belongs_to_collection': {'id': 544670, 'name': 'Sing Collection', 'poster_path': '/h151oRzvsxfKRznEmlQJRlnvsid.jpg', 'backdrop_path': '/z9ft5HYHzWcasR6SGcgeluxTznB.jpg'}, 'budget': 85000000, 'genres': [{'id': 16, 'name': 'Animation'}, {'id': 10751, 'name': 'Family'}, {'id': 10402, 'name': 'Music'}, {'id': 35, 'name': 'Comedy'}], 'homepage': 'https://www.illumination.com/movie/sing-2/', 'id': 438695, 'imdb_id': 'tt6467266', 'origin_country': ['US'], 'original_language': 'en', 'original_title': 'Sing 2', 'overview': 'Buster and his new cast now have their sights set on debuting a new show at the Crystal Tower Theater in glamorous Redshore City. But with no connections, he and his singers must sneak into the Crystal Entertainment offices, run by the ruthless wolf mogul Jimmy Crystal, where the gang pitches the ridiculous idea of casting the lion rock legend Clay Calloway in their show.

Search result for 'The Tragedy of Macbeth': {'page': 1, 'results': [{'adult': False, 'backdrop_path': '/lMjY6kMBOHhloz2Ul16fLJn8xuw.jpg', 'genre_ids': [18, 10752], 'id': 591538, 'original_language': 'en', 'original_title': 'The Tragedy of Macbeth', 'overview': 'Macbeth, the Thane of Glamis, receives a prophecy from a trio of witches that one day he will become King of Scotland. Consumed by ambition and spurred to action by his wife, Macbeth murders his king and takes the throne for himself.', 'popularity': 28.782, 'poster_path': '/tDNJEhcLbX3jIk3BMCur9pCdaVD.jpg', 'release_date': '2021-12-05', 'title': 'The Tragedy of Macbeth', 'video': False, 'vote_average': 6.955, 'vote_count': 721}, {'adult': False, 'backdrop_path': '/tiufG6kHsUPFSHTDncLjaavhepr.jpg', 'genre_ids': [27, 36, 18], 'id': 885048, 'original_language': 'en', 'original_title': 'The Tragedy of Macbeth', 'overview': "Following one couple's spine-chilling quest for power, this performance was captured during its original run a

Search result for 'Memoria': {'page': 1, 'results': [{'adult': False, 'backdrop_path': '/nvTD2DO96mEwOga34lQZgBKpdEQ.jpg', 'genre_ids': [18, 878, 9648], 'id': 511819, 'original_language': 'es', 'original_title': 'Memoria', 'overview': 'One morning, Jessica Holland, a Scottish orchid farmer visiting her sister in Bogotá, is woken by a loud ‘bang’. This haunting sound dispels her sleep for days, calling into question her identity and guiding her from recording studios to secluded jungle villages in an attempt to find its source.', 'popularity': 21.328, 'poster_path': '/mkJl2dVJnPgWAALCuIXJ61TlwHf.jpg', 'release_date': '2021-09-30', 'title': 'Memoria', 'video': False, 'vote_average': 6.0, 'vote_count': 205}, {'adult': False, 'backdrop_path': '/sDOvwWRTYEAQDnzSKHUqbwqgGTd.jpg', 'genre_ids': [16, 10749], 'id': 1195421, 'original_language': 'en', 'original_title': 'Memoria', 'overview': 'The memories of a man and a woman come to life through photography and animation.', 'popularity': 1.07, '

c:\users\paras rana\appdata\local\programs\python\python37\lib\site-packages\ipykernel_launcher.py:33: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy


In [47]:
df_2021

Title  \
0                Shadow in the Cloud   
1                            Hacksaw   
2    Dr. Bird's Advice for Sad Poets   
3                    The White Tiger   
4                        Locked Down   
..                               ...   
359                   The King's Man   
360           The Tragedy of Macbeth   
361             A Journal for Jordan   
362                American Underdog   
363                          Memoria   

                                         Cast and crew  \
0    Roseanne Liang (director/screenplay); Max Land...   
1    Anthony Leone (director/screenplay); Amy Cay, ...   
2    Yaniv Raz (director/screenplay); Lucas Jade Zu...   
3    Ramin Bahrani (director/screenplay); Adarsh Go...   
4    Doug Liman (director); Steven Knight (screenpl...   
..                                                 ...   
359  Matthew Vaughn (director/screenplay); Karl Gaj...   
360  Joel Coen (director/screenplay); Denzel Washin...   
361  Denzel Washington (director); Virgil Williams ...   
362  Erwin brothers (directors); Jon Erwin, David A...   
363  Apichatpong Weerasethakul (director/acreenplay...   

                                genres  
0                    Horror Action War  
1    Adventure Family TV Movie Western  
2                         Comedy Drama  
3                                Drama  
4                 Comedy Crime Romance  
..                                 ...  
359   Action Comedy Adventure Thriller  
360                          Drama War  
361                      Drama Romance  
362                              Drama  
363      Drama Science Fiction Mystery  

[364 rows x 3 columns]

In [48]:
def get_director1(x):
    if " (director)" in x:
        return x.split(" (director)")[0]
    elif " (directors)" in x:
        return x.split(" (directors)")[0]
    elif " (directors/screenplay)" in x:
        return x.split(" (directors/screenplay)")[0]
    elif " (director/screenwriter)" in x:
        return x.split(" (director/screenwriter)")[0]
    elif " (director/screenplay[119])" in x:
        return x.split(" (director/screenplay[119])")[0]
    elif " (director[177])" in x:
        return x.split(" (director[177])")[0]
    elif " (director,screenplay)" in x:
        return x.split(" (director,screenplay)")[0]
    else:
        return x.split(" (director/screenplay)")[0]

In [49]:
df_2021['director_name'] = df_2021['Cast and crew'].map(lambda x: get_director1(x))

c:\users\paras rana\appdata\local\programs\python\python37\lib\site-packages\ipykernel_launcher.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  """Entry point for launching an IPython kernel.


In [50]:
df_2021['actor_1_name'] = df_2021['Cast and crew'].map(lambda x: get_actor1(x))

c:\users\paras rana\appdata\local\programs\python\python37\lib\site-packages\ipykernel_launcher.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  """Entry point for launching an IPython kernel.


In [51]:
df_2021['actor_2_name'] = df_2021['Cast and crew'].map(lambda x: get_actor2(x))

c:\users\paras rana\appdata\local\programs\python\python37\lib\site-packages\ipykernel_launcher.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  """Entry point for launching an IPython kernel.


In [52]:
df_2021['actor_3_name'] = df_2021['Cast and crew'].map(lambda x: get_actor3(x))

c:\users\paras rana\appdata\local\programs\python\python37\lib\site-packages\ipykernel_launcher.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  """Entry point for launching an IPython kernel.


In [53]:
df_2021

Title  \
0                Shadow in the Cloud   
1                            Hacksaw   
2    Dr. Bird's Advice for Sad Poets   
3                    The White Tiger   
4                        Locked Down   
..                               ...   
359                   The King's Man   
360           The Tragedy of Macbeth   
361             A Journal for Jordan   
362                American Underdog   
363                          Memoria   

                                         Cast and crew  \
0    Roseanne Liang (director/screenplay); Max Land...   
1    Anthony Leone (director/screenplay); Amy Cay, ...   
2    Yaniv Raz (director/screenplay); Lucas Jade Zu...   
3    Ramin Bahrani (director/screenplay); Adarsh Go...   
4    Doug Liman (director); Steven Knight (screenpl...   
..                                                 ...   
359  Matthew Vaughn (director/screenplay); Karl Gaj...   
360  Joel Coen (director/screenplay); Denzel Washin...   
361  Denzel Washington (director); Virgil Williams ...   
362  Erwin brothers (directors); Jon Erwin, David A...   
363  Apichatpong Weerasethakul (director/acreenplay...   

                                genres  \
0                    Horror Action War   
1    Adventure Family TV Movie Western   
2                         Comedy Drama   
3                                Drama   
4                 Comedy Crime Romance   
..                                 ...   
359   Action Comedy Adventure Thriller   
360                          Drama War   
361                      Drama Romance   
362                              Drama   
363      Drama Science Fiction Mystery   

                                         director_name  \
0                                       Roseanne Liang   
1                                        Anthony Leone   
2                                            Yaniv Raz   
3                                        Ramin Bahrani   
4                                           Doug Liman   
..                                                 ...   
359                                     Matthew Vaughn   
360                                          Joel Coen   
361                                  Denzel Washington   
362                                     Erwin brothers   
363  Apichatpong Weerasethakul (director/acreenplay...   

                                          actor_1_name          actor_2_name  \
0                                   Chloë Grace Moretz     Taylor John Smith   
1                                              Amy Cay  Brian Patrick Butler   
2                                    Lucas Jade Zumann        Taylor Russell   
3                                        Adarsh Gourav         Rajkummar Rao   
4                                        Anne Hathaway      Chiwetel Ejiofor   
..                                                 ...                   ...   
359                                      Ralph Fiennes        Gemma Arterton   
360                                  Denzel Washington     Frances McDormand   
361                                  Michael B. Jordan          Chanté Adams   
362                                       Zachary Levi           Anna Paquin   
363  Apichatpong Weerasethakul (director/acreenplay...            Elkin Díaz   

              actor_3_name  
0             Beulah Koale  
1       Michael C. Burgess  
2             Chase Stokes  
3    Priyanka Chopra Jonas  
4         Stephen Merchant  
..                     ...  
359             Rhys Ifans  
360          Bertie Carvel  
361        Jalon Christian  
362           Dennis Quaid  
363         Jeanne Balibar  

[364 rows x 7 columns]

In [54]:
df_2021 = df_2021.rename(columns = {'Title':'movie_title'})

In [55]:
newdf_2021 = df_2021.loc[: , ['director_name' , 'actor_1_name' , 'actor_2_name' , 'actor_3_name' , 'genres' , 'movie_title']]

In [56]:
newdf_2021

director_name  \
0                                       Roseanne Liang   
1                                        Anthony Leone   
2                                            Yaniv Raz   
3                                        Ramin Bahrani   
4                                           Doug Liman   
..                                                 ...   
359                                     Matthew Vaughn   
360                                          Joel Coen   
361                                  Denzel Washington   
362                                     Erwin brothers   
363  Apichatpong Weerasethakul (director/acreenplay...   

                                          actor_1_name          actor_2_name  \
0                                   Chloë Grace Moretz     Taylor John Smith   
1                                              Amy Cay  Brian Patrick Butler   
2                                    Lucas Jade Zumann        Taylor Russell   
3                                        Adarsh Gourav         Rajkummar Rao   
4                                        Anne Hathaway      Chiwetel Ejiofor   
..                                                 ...                   ...   
359                                      Ralph Fiennes        Gemma Arterton   
360                                  Denzel Washington     Frances McDormand   
361                                  Michael B. Jordan          Chanté Adams   
362                                       Zachary Levi           Anna Paquin   
363  Apichatpong Weerasethakul (director/acreenplay...            Elkin Díaz   

              actor_3_name                             genres  \
0             Beulah Koale                  Horror Action War   
1       Michael C. Burgess  Adventure Family TV Movie Western   
2             Chase Stokes                       Comedy Drama   
3    Priyanka Chopra Jonas                              Drama   
4         Stephen Merchant               Comedy Crime Romance   
..                     ...                                ...   
359             Rhys Ifans   Action Comedy Adventure Thriller   
360          Bertie Carvel                          Drama War   
361        Jalon Christian                      Drama Romance   
362           Dennis Quaid                              Drama   
363         Jeanne Balibar      Drama Science Fiction Mystery   

                         movie_title  
0                Shadow in the Cloud  
1                            Hacksaw  
2    Dr. Bird's Advice for Sad Poets  
3                    The White Tiger  
4                        Locked Down  
..                               ...  
359                   The King's Man  
360           The Tragedy of Macbeth  
361             A Journal for Jordan  
362                American Underdog  
363                          Memoria  

[364 rows x 6 columns]

In [57]:
newdf_2021['comb'] = newdf_2021['actor_1_name'] + ' ' + newdf_2021['actor_2_name'] + ' ' + newdf_2021['actor_3_name'] + ' ' + newdf_2021['director_name'] + ' ' + newdf_2021['genres']

In [58]:
newdf_2021

director_name  \
0                                       Roseanne Liang   
1                                        Anthony Leone   
2                                            Yaniv Raz   
3                                        Ramin Bahrani   
4                                           Doug Liman   
..                                                 ...   
359                                     Matthew Vaughn   
360                                          Joel Coen   
361                                  Denzel Washington   
362                                     Erwin brothers   
363  Apichatpong Weerasethakul (director/acreenplay...   

                                          actor_1_name          actor_2_name  \
0                                   Chloë Grace Moretz     Taylor John Smith   
1                                              Amy Cay  Brian Patrick Butler   
2                                    Lucas Jade Zumann        Taylor Russell   
3                                        Adarsh Gourav         Rajkummar Rao   
4                                        Anne Hathaway      Chiwetel Ejiofor   
..                                                 ...                   ...   
359                                      Ralph Fiennes        Gemma Arterton   
360                                  Denzel Washington     Frances McDormand   
361                                  Michael B. Jordan          Chanté Adams   
362                                       Zachary Levi           Anna Paquin   
363  Apichatpong Weerasethakul (director/acreenplay...            Elkin Díaz   

              actor_3_name                             genres  \
0             Beulah Koale                  Horror Action War   
1       Michael C. Burgess  Adventure Family TV Movie Western   
2             Chase Stokes                       Comedy Drama   
3    Priyanka Chopra Jonas                              Drama   
4         Stephen Merchant               Comedy Crime Romance   
..                     ...                                ...   
359             Rhys Ifans   Action Comedy Adventure Thriller   
360          Bertie Carvel                          Drama War   
361        Jalon Christian                      Drama Romance   
362           Dennis Quaid                              Drama   
363         Jeanne Balibar      Drama Science Fiction Mystery   

                         movie_title  \
0                Shadow in the Cloud   
1                            Hacksaw   
2    Dr. Bird's Advice for Sad Poets   
3                    The White Tiger   
4                        Locked Down   
..                               ...   
359                   The King's Man   
360           The Tragedy of Macbeth   
361             A Journal for Jordan   
362                American Underdog   
363                          Memoria   

                                                  comb  
0    Chloë Grace Moretz Taylor John Smith Beulah Ko...  
1    Amy Cay Brian Patrick Butler Michael C. Burges...  
2    Lucas Jade Zumann Taylor Russell Chase Stokes ...  
3    Adarsh Gourav Rajkummar Rao Priyanka Chopra Jo...  
4    Anne Hathaway Chiwetel Ejiofor Stephen Merchan...  
..                                                 ...  
359  Ralph Fiennes Gemma Arterton Rhys Ifans Matthe...  
360  Denzel Washington Frances McDormand Bertie Car...  
361  Michael B. Jordan Chanté Adams Jalon Christian...  
362  Zachary Levi Anna Paquin Dennis Quaid Erwin br...  
363  Apichatpong Weerasethakul (director/acreenplay...  

[364 rows x 7 columns]

In [59]:
newdf_2021['movie_title'] = newdf_2021['movie_title'].str.lower()

In [60]:
newdf_2021

director_name  \
0                                       Roseanne Liang   
1                                        Anthony Leone   
2                                            Yaniv Raz   
3                                        Ramin Bahrani   
4                                           Doug Liman   
..                                                 ...   
359                                     Matthew Vaughn   
360                                          Joel Coen   
361                                  Denzel Washington   
362                                     Erwin brothers   
363  Apichatpong Weerasethakul (director/acreenplay...   

                                          actor_1_name          actor_2_name  \
0                                   Chloë Grace Moretz     Taylor John Smith   
1                                              Amy Cay  Brian Patrick Butler   
2                                    Lucas Jade Zumann        Taylor Russell   
3                                        Adarsh Gourav         Rajkummar Rao   
4                                        Anne Hathaway      Chiwetel Ejiofor   
..                                                 ...                   ...   
359                                      Ralph Fiennes        Gemma Arterton   
360                                  Denzel Washington     Frances McDormand   
361                                  Michael B. Jordan          Chanté Adams   
362                                       Zachary Levi           Anna Paquin   
363  Apichatpong Weerasethakul (director/acreenplay...            Elkin Díaz   

              actor_3_name                             genres  \
0             Beulah Koale                  Horror Action War   
1       Michael C. Burgess  Adventure Family TV Movie Western   
2             Chase Stokes                       Comedy Drama   
3    Priyanka Chopra Jonas                              Drama   
4         Stephen Merchant               Comedy Crime Romance   
..                     ...                                ...   
359             Rhys Ifans   Action Comedy Adventure Thriller   
360          Bertie Carvel                          Drama War   
361        Jalon Christian                      Drama Romance   
362           Dennis Quaid                              Drama   
363         Jeanne Balibar      Drama Science Fiction Mystery   

                         movie_title  \
0                shadow in the cloud   
1                            hacksaw   
2    dr. bird's advice for sad poets   
3                    the white tiger   
4                        locked down   
..                               ...   
359                   the king's man   
360           the tragedy of macbeth   
361             a journal for jordan   
362                american underdog   
363                          memoria   

                                                  comb  
0    Chloë Grace Moretz Taylor John Smith Beulah Ko...  
1    Amy Cay Brian Patrick Butler Michael C. Burges...  
2    Lucas Jade Zumann Taylor Russell Chase Stokes ...  
3    Adarsh Gourav Rajkummar Rao Priyanka Chopra Jo...  
4    Anne Hathaway Chiwetel Ejiofor Stephen Merchan...  
..                                                 ...  
359  Ralph Fiennes Gemma Arterton Rhys Ifans Matthe...  
360  Denzel Washington Frances McDormand Bertie Car...  
361  Michael B. Jordan Chanté Adams Jalon Christian...  
362  Zachary Levi Anna Paquin Dennis Quaid Erwin br...  
363  Apichatpong Weerasethakul (director/acreenplay...  

[364 rows x 7 columns]

In [61]:
newdf_2021.isna().sum()

director_name     0
actor_1_name      0
actor_2_name      7
actor_3_name     25
genres            1
movie_title       0
comb             26
dtype: int64

In [62]:
newdf_2021 = newdf_2021.dropna(how='any')

In [63]:
newdf_2021.isna().sum()

director_name    0
actor_1_name     0
actor_2_name     0
actor_3_name     0
genres           0
movie_title      0
comb             0
dtype: int64

In [64]:
newdf_2021

director_name  \
0                                       Roseanne Liang   
1                                        Anthony Leone   
2                                            Yaniv Raz   
3                                        Ramin Bahrani   
4                                           Doug Liman   
..                                                 ...   
359                                     Matthew Vaughn   
360                                          Joel Coen   
361                                  Denzel Washington   
362                                     Erwin brothers   
363  Apichatpong Weerasethakul (director/acreenplay...   

                                          actor_1_name          actor_2_name  \
0                                   Chloë Grace Moretz     Taylor John Smith   
1                                              Amy Cay  Brian Patrick Butler   
2                                    Lucas Jade Zumann        Taylor Russell   
3                                        Adarsh Gourav         Rajkummar Rao   
4                                        Anne Hathaway      Chiwetel Ejiofor   
..                                                 ...                   ...   
359                                      Ralph Fiennes        Gemma Arterton   
360                                  Denzel Washington     Frances McDormand   
361                                  Michael B. Jordan          Chanté Adams   
362                                       Zachary Levi           Anna Paquin   
363  Apichatpong Weerasethakul (director/acreenplay...            Elkin Díaz   

              actor_3_name                             genres  \
0             Beulah Koale                  Horror Action War   
1       Michael C. Burgess  Adventure Family TV Movie Western   
2             Chase Stokes                       Comedy Drama   
3    Priyanka Chopra Jonas                              Drama   
4         Stephen Merchant               Comedy Crime Romance   
..                     ...                                ...   
359             Rhys Ifans   Action Comedy Adventure Thriller   
360          Bertie Carvel                          Drama War   
361        Jalon Christian                      Drama Romance   
362           Dennis Quaid                              Drama   
363         Jeanne Balibar      Drama Science Fiction Mystery   

                         movie_title  \
0                shadow in the cloud   
1                            hacksaw   
2    dr. bird's advice for sad poets   
3                    the white tiger   
4                        locked down   
..                               ...   
359                   the king's man   
360           the tragedy of macbeth   
361             a journal for jordan   
362                american underdog   
363                          memoria   

                                                  comb  
0    Chloë Grace Moretz Taylor John Smith Beulah Ko...  
1    Amy Cay Brian Patrick Butler Michael C. Burges...  
2    Lucas Jade Zumann Taylor Russell Chase Stokes ...  
3    Adarsh Gourav Rajkummar Rao Priyanka Chopra Jo...  
4    Anne Hathaway Chiwetel Ejiofor Stephen Merchan...  
..                                                 ...  
359  Ralph Fiennes Gemma Arterton Rhys Ifans Matthe...  
360  Denzel Washington Frances McDormand Bertie Car...  
361  Michael B. Jordan Chanté Adams Jalon Christian...  
362  Zachary Levi Anna Paquin Dennis Quaid Erwin br...  
363  Apichatpong Weerasethakul (director/acreenplay...  

[338 rows x 7 columns]

In [65]:
my_df = newdf_2020.append(newdf_2021 , ignore_index=True)

In [66]:
my_df

director_name  \
0                                        Nicolas Pesce   
1                                       William Eubank   
2                                        Miguel Arteta   
3                                            Jon Avnet   
4                                       Anthony Jerjen   
..                                                 ...   
579                                     Matthew Vaughn   
580                                          Joel Coen   
581                                  Denzel Washington   
582                                     Erwin brothers   
583  Apichatpong Weerasethakul (director/acreenplay...   

                                          actor_1_name       actor_2_name  \
0                                   Andrea Riseborough      Demián Bichir   
1                                      Kristen Stewart     Vincent Cassel   
2                                      Tiffany Haddish         Rose Byrne   
3                                         Richard Gere     Peter Dinklage   
4                                        Josh Hartnett  Margarita Levieva   
..                                                 ...                ...   
579                                      Ralph Fiennes     Gemma Arterton   
580                                  Denzel Washington  Frances McDormand   
581                                  Michael B. Jordan       Chanté Adams   
582                                       Zachary Levi        Anna Paquin   
583  Apichatpong Weerasethakul (director/acreenplay...         Elkin Díaz   

        actor_3_name                                   genres  \
0           John Cho                  Horror Mystery Thriller   
1    Jessica Henwick  Horror Science Fiction Action Adventure   
2        Salma Hayek                                   Comedy   
3     Walton Goggins                                    Drama   
4     Chandler Riggs                     Crime Thriller Drama   
..               ...                                      ...   
579       Rhys Ifans         Action Comedy Adventure Thriller   
580    Bertie Carvel                                Drama War   
581  Jalon Christian                            Drama Romance   
582     Dennis Quaid                                    Drama   
583   Jeanne Balibar            Drama Science Fiction Mystery   

                movie_title                                               comb  
0                the grudge  Andrea Riseborough Demián Bichir John Cho Nico...  
1                underwater  Kristen Stewart Vincent Cassel Jessica Henwick...  
2               like a boss  Tiffany Haddish Rose Byrne Salma Hayek Miguel ...  
3             three christs  Richard Gere Peter Dinklage Walton Goggins Jon...  
4         inherit the viper  Josh Hartnett Margarita Levieva Chandler Riggs...  
..                      ...                                                ...  
579          the king's man  Ralph Fiennes Gemma Arterton Rhys Ifans Matthe...  
580  the tragedy of macbeth  Denzel Washington Frances McDormand Bertie Car...  
581    a journal for jordan  Michael B. Jordan Chanté Adams Jalon Christian...  
582       american underdog  Zachary Levi Anna Paquin Dennis Quaid Erwin br...  
583                 memoria  Apichatpong Weerasethakul (director/acreenplay...  

[584 rows x 7 columns]

In [67]:
old_df = pd.read_csv("final_data.csv")

In [68]:
old_df

director_name       actor_1_name          actor_2_name  \
0              James Cameron        CCH Pounder      Joel David Moore   
1             Gore Verbinski        Johnny Depp         Orlando Bloom   
2                 Sam Mendes    Christoph Waltz          Rory Kinnear   
3          Christopher Nolan          Tom Hardy        Christian Bale   
4                Doug Walker        Doug Walker            Rob Walker   
...                      ...                ...                   ...   
5855  Nick Bruno, Troy Quane         Will Smith           Tom Holland   
5856            Greta Gerwig      Saoirse Ronan           Emma Watson   
5857              Sam Mendes      George MacKay  Dean-Charles Chapman   
5858   Destin Daniel Cretton  Michael B. Jordan            Jamie Foxx   
5859         Chinonye Chukwu      Alfre Woodard        Wendell Pierce   

              actor_3_name                           genres  \
0                Wes Studi  Action Adventure Fantasy Sci-Fi   
1           Jack Davenport         Action Adventure Fantasy   
2         Stephanie Sigman        Action Adventure Thriller   
3     Joseph Gordon-Levitt                  Action Thriller   
4                  unknown                      Documentary   
...                    ...                              ...   
5855         Rashida Jones                        Animation   
5856         Florence Pugh                            Drama   
5857           Mark Strong                              War   
5858           Brie Larson                            Drama   
5859           Aldis Hodge                            Drama   

                                            movie_title  \
0                                                avatar   
1              pirates of the caribbean: at world's end   
2                                               spectre   
3                                 the dark knight rises   
4     star wars: episode vii - the force awakens    ...   
...                                                 ...   
5855                                  spies in disguise   
5856                                       little women   
5857                                               1917   
5858                                         just mercy   
5859                                           clemency   

                                                   comb  
0     CCH Pounder Joel David Moore Wes Studi James C...  
1     Johnny Depp Orlando Bloom Jack Davenport Gore ...  
2     Christoph Waltz Rory Kinnear Stephanie Sigman ...  
3     Tom Hardy Christian Bale Joseph Gordon-Levitt ...  
4     Doug Walker Rob Walker unknown Doug Walker Doc...  
...                                                 ...  
5855  Will Smith Tom Holland Rashida Jones Nick Brun...  
5856  Saoirse Ronan Emma Watson Florence Pugh Greta ...  
5857  George MacKay Dean-Charles Chapman Mark Strong...  
5858  Michael B. Jordan Jamie Foxx Brie Larson Desti...  
5859  Alfre Woodard Wendell Pierce Aldis Hodge Chino...  

[5860 rows x 7 columns]

In [69]:
final_df = old_df.append(my_df , ignore_index=True)

In [70]:
final_df

director_name  \
0                                         James Cameron   
1                                        Gore Verbinski   
2                                            Sam Mendes   
3                                     Christopher Nolan   
4                                           Doug Walker   
...                                                 ...   
6439                                     Matthew Vaughn   
6440                                          Joel Coen   
6441                                  Denzel Washington   
6442                                     Erwin brothers   
6443  Apichatpong Weerasethakul (director/acreenplay...   

                                           actor_1_name       actor_2_name  \
0                                           CCH Pounder   Joel David Moore   
1                                           Johnny Depp      Orlando Bloom   
2                                       Christoph Waltz       Rory Kinnear   
3                                             Tom Hardy     Christian Bale   
4                                           Doug Walker         Rob Walker   
...                                                 ...                ...   
6439                                      Ralph Fiennes     Gemma Arterton   
6440                                  Denzel Washington  Frances McDormand   
6441                                  Michael B. Jordan       Chanté Adams   
6442                                       Zachary Levi        Anna Paquin   
6443  Apichatpong Weerasethakul (director/acreenplay...         Elkin Díaz   

              actor_3_name                            genres  \
0                Wes Studi   Action Adventure Fantasy Sci-Fi   
1           Jack Davenport          Action Adventure Fantasy   
2         Stephanie Sigman         Action Adventure Thriller   
3     Joseph Gordon-Levitt                   Action Thriller   
4                  unknown                       Documentary   
...                    ...                               ...   
6439            Rhys Ifans  Action Comedy Adventure Thriller   
6440         Bertie Carvel                         Drama War   
6441       Jalon Christian                     Drama Romance   
6442          Dennis Quaid                             Drama   
6443        Jeanne Balibar     Drama Science Fiction Mystery   

                                            movie_title  \
0                                                avatar   
1              pirates of the caribbean: at world's end   
2                                               spectre   
3                                 the dark knight rises   
4     star wars: episode vii - the force awakens    ...   
...                                                 ...   
6439                                     the king's man   
6440                             the tragedy of macbeth   
6441                               a journal for jordan   
6442                                  american underdog   
6443                                            memoria   

                                                   comb  
0     CCH Pounder Joel David Moore Wes Studi James C...  
1     Johnny Depp Orlando Bloom Jack Davenport Gore ...  
2     Christoph Waltz Rory Kinnear Stephanie Sigman ...  
3     Tom Hardy Christian Bale Joseph Gordon-Levitt ...  
4     Doug Walker Rob Walker unknown Doug Walker Doc...  
...                                                 ...  
6439  Ralph Fiennes Gemma Arterton Rhys Ifans Matthe...  
6440  Denzel Washington Frances McDormand Bertie Car...  
6441  Michael B. Jordan Chanté Adams Jalon Christian...  
6442  Zachary Levi Anna Paquin Dennis Quaid Erwin br...  
6443  Apichatpong Weerasethakul (director/acreenplay...  

[6444 rows x 7 columns]

In [71]:
final_df.isna().sum()

director_name    0
actor_1_name     0
actor_2_name     0
actor_3_name     0
genres           0
movie_title      0
comb             0
dtype: int64

In [72]:
final_df.to_csv("final_1.csv" , index=False)